#### Introdução à Base de Dados do Airbnb

O conjunto de dados "Inside Airbnb", disponível no website "http://insideairbnb.com/", é uma valiosa fonte de informações sobre listagens de hospedagem, avaliações de hóspedes e disponibilidade de calendário em várias cidades ao redor do mundo, incluindo o Rio de Janeiro. Antes de prosseguirmos com a engenharia de dados, é importante entender os principais componentes deste conjunto de dados:

1. **Listing (Listagem):** Este conjunto de dados contém informações detalhadas sobre as propriedades listadas no Airbnb. Cada registro representa uma listagem individual e inclui informações como o tipo de propriedade, preço, localização, número de quartos, comodidades oferecidas e muito mais.

2. **Reviews (Avaliações):** O conjunto de dados de avaliações contém informações sobre as avaliações feitas por hóspedes que ficaram nas propriedades listadas. Ele inclui dados como a data da avaliação, o identificador da propriedade, os comentários escritos pelos hóspedes, e outras informações. 

3. **Calendar (Calendário):** Este conjunto de dados contém informações sobre a disponibilidade das propriedades ao longo do tempo. Ele lista as datas em que as propriedades estão disponíveis para reserva, bem como os preços para cada data.

O dicionário dos dados também está disponível no website: "http://insideairbnb.com/".

#### Passos do Projeto

1. **Aquisição de Dados e Armazenamento de Dados em PostgreSQL - Camada Bronze**
   - Baixe o conjunto de dados "Inside Airbnb" do Rio de Janeiro da fonte oficial (http://insideairbnb.com/) e promova uma estruturação simples nos dados.
   - Crie um banco de dados PostgreSQL para armazenar os dados brutos das 3 tabelas ("Listing", "Reviews" e Calendar") na camada "bronze".

<br>

2. **Data Clean - Camada Silver:**
   - Identifique e lide com valores ausentes, duplicatas e outliers nos dados brutos da camada "bronze".
   - Padronize e limpe os nomes das colunas, convertendo-os em um formato consistente.
   - Realize uma limpeza textual em campos, como descrições de propriedades, removendo caracteres especiais e erros de digitação.

<br>

3. **Data Quality - Camada Silver:**
   - Defina métricas de qualidade de dados, como integridade, precisão e consistência para os dados da camada "bronze".
   - Implemente verificações para garantir que os dados da camada "silver" estejam em conformidade com essas métricas.
   - Estabeleça um sistema de monitoramento contínuo da qualidade dos dados da camada "silver".

<br>

4. **Testes de Qualidade - Camada Silver:**
   - Utilize a biblioteca Great Expectations para criar testes de qualidade automatizados que verifiquem as expectativas definidas para os dados da camada "silver".
   - Desenvolva testes que assegurem que os dados da camada "silver" atendam às regras de negócios e aos requisitos de qualidade.

<br>

5. **Transformação de Dados com dbt - Camada Silver:**
   - Utilize a ferramenta dbt para criar a camada "silver" de dados, realizando transformações e preparando os dados da camada em questão.
   - Mantenha um controle de versão dos modelos dbt relacionados à camada "silver" e automatize a execução das transformações.

<br>

6. **Armazenamento de Dados em PostgreSQL - Camada Silver:**
   - Armazene os dados da camada "silver" no mesmo banco de dados PostgreSQL.
   - Estabeleça conexões entre o dbt e o PostgreSQL para carregar os dados transformados da camada "silver" no banco.

<br>

7. **Validação de Expectativas com Great Expectations - Camada Silver:**
   - Implemente validações adicionais usando Great Expectations nas camadas de dados da camada "silver".
   - Monitore a qualidade dos dados da camada "silver" após cada transformação e ajuste os testes de acordo.

<br>

8. **Transformação de Dados com dbt - Camada Gold:**
   - Utilize o dbt para criar a camada "gold" de dados, aplicando agregações especializadas, como médias de preços por propriedade, por período, e outras agregações especializadas.
   - Mantenha um controle de versão dos modelos dbt relacionados à camada "gold" e automatize a execução das transformações.
   - Armazene os dados da camada "gold" no mesmo banco de dados PostgreSQL, mantendo a estrutura de dados otimizada para consultas analíticas.

<br>

 9. **Apresentação e Discussão:**
    - Apresente os resultados do projeto para a turma, enfatizando os aspectos de engenharia de dados, qualidade de dados e uso de ferramentas como dbt, Great Expectations e o armazenamento em um banco de dados PostgreSQL nas camadas "bronze", "silver" e "gold".


Bibliotecas

In [1]:
# Importando as bibliotecas
import requests
import io
import re
import pandas as pd
import sqlalchemy as sqlal
from sqlalchemy import create_engine, text as sql_text
#from ydata_profiling import ProfileReport

Função para aquisição dos dados

In [2]:
# Definindo as URLs para baixar os dados
url1 = "http://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2023-09-22/data/listings.csv.gz"
url2 = "http://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2023-09-22/data/calendar.csv.gz"
url3 = "http://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2023-09-22/data/reviews.csv.gz"

# Função para baixar e carregar o arquivo em um dataframe
def download_df(url):
    response = requests.get(url)
    if response.status_code == 200:
        file_buffer = io.BytesIO(response.content)
        df = pd.read_csv(file_buffer, compression='gzip')
        return df
    else:
        print(f"Falha ao baixar o arquivo de {url}")
        return None

Adquirindo e verificando os dados

In [3]:
# Baixando e carregando os três arquivos
listings = download_df(url1)
calendar = download_df(url2)
reviews = download_df(url3)

In [ ]:
display(listings)

In [ ]:
calendar

In [ ]:
reviews

SQL

In [28]:
%run ./create_engine.ipynb

Bronze

In [11]:
# Enviando os dados para o banco de dados
listings.to_sql('airbnb_listings', engine, if_exists='replace', index=False)
calendar.to_sql('airbnb_calendar', engine, if_exists='replace', index=False)
reviews.to_sql('airbnb_reviews', engine, if_exists='replace', index=False)

307

In [ ]:
# Função para remover duplicatas
def remove_duplicates(df):
    print("N. de linhas antes de remover duplicadas:", len(df))
    df = df.drop_duplicates()
    print("N. de linhas depois de remover duplicadas:", len(df))
    

# Função para verificar os casos nulos
def check_miss(df):
    df_miss = df.isna().sum()  # soma a quantidade de valores nulos em cada coluna
    df_miss = (df_miss/len(df))*100 # calcula o percentual de casos nulos
    df_miss.sort_values(ascending=False) # ordena pelas colunas com mais casos nulos
    
    return df_miss


def remove_constant(df):
    list_constant = [col for col in df.columns if df[col].nunique() == 1]
    list_constant
    print("N. de colunas antes de remover colunas constantes:", len(df.columns))
    df = df.drop(list_constant, axis=1)
    print("N. de colunas depois de remover colunas constantes:", len(df.columns))
    
def verify_unbalanced(df):
    list_imbalance = []
    limit = 0.98
    for col in df.columns:
        counts = df[col].value_counts(normalize=True)
        if len(counts) >= 2:  # Verifica se há pelo menos dois valores distintos
            perc = counts.values[0]
            if perc > limit:
                list_imbalance.append(col)
                print(col, perc)
            
    return list_imbalance


def remove_unbalanced(df):
    list_imbalance = verify_unbalanced(df)
            
    df = df.drop(list_imbalance, axis=1)

# Transformações

In [8]:
# Função para remover duplicatas
def remove_duplicates(df):
    print("N. de linhas antes de remover duplicadas:", len(df))
    df = df.drop_duplicates()
    print("N. de linhas depois de remover duplicadas:", len(df))

In [9]:
# Função para verificar os casos nulos
def check_miss(df):
    df_miss = df.isna().sum()  # soma a quantidade de valores nulos em cada coluna
    df_miss = (df_miss/len(df))*100 # calcula o percentual de casos nulos
    df_miss.sort_values(ascending=False) # ordena pelas colunas com mais casos nulos
    
    return df_miss

In [10]:
# Função para remover as colunas constantes
def remove_constant(df):
    list_constant = [col for col in df.columns if df[col].nunique() == 1]
    list_constant
    print("N. de colunas antes de remover colunas constantes:", len(df.columns))
    df = df.drop(list_constant, axis=1)
    print("N. de colunas depois de remover colunas constantes:", len(df.columns))

In [11]:
# Função para verificar as colunas desbalanceados
def verify_unbalanced(df):
    list_imbalance = []
    limit = 0.98
    for col in df.columns:
        counts = df[col].value_counts(normalize=True)
        if len(counts) >= 2:  # Verifica se há pelo menos dois valores distintos
            perc = counts.values[0]
            if perc > limit:
                list_imbalance.append(col)
                print(col, perc)
            
    return list_imbalance

In [12]:
# Função para remover as colunas desbalanceados
def remove_unbalanced(df):
    list_imbalance = verify_unbalanced(df)
            
    df = df.drop(list_imbalance, axis=1)

Listings

In [6]:
listings.dtypes

id                                                int64
listing_url                                      object
scrape_id                                         int64
last_scraped                                     object
source                                           object
                                                 ...   
calculated_host_listings_count                    int64
calculated_host_listings_count_entire_homes       int64
calculated_host_listings_count_private_rooms      int64
calculated_host_listings_count_shared_rooms       int64
reviews_per_month                               float64
Length: 75, dtype: object

In [13]:
remove_duplicates(listings)

N. de linhas antes de remover duplicadas: 31964
N. de linhas depois de remover duplicadas: 31964


In [14]:
check_miss(listings)


id                                               0.000000
listing_url                                      0.000000
scrape_id                                        0.000000
last_scraped                                     0.000000
source                                           0.000000
                                                  ...    
calculated_host_listings_count                   0.000000
calculated_host_listings_count_entire_homes      0.000000
calculated_host_listings_count_private_rooms     0.000000
calculated_host_listings_count_shared_rooms      0.000000
reviews_per_month                               25.466149
Length: 75, dtype: float64

In [15]:
remove_constant(listings)


N. de colunas antes de remover colunas constantes: 75
N. de colunas depois de remover colunas constantes: 74


In [16]:
verify_unbalanced(listings)

[]

In [17]:
listings_num = listings.select_dtypes(include=['number'])

In [19]:
# Cria um relatório ProfileReport do dataframe
listings_profile = ProfileReport(listings_num, title="'Listings' Profiling Report", minimal=True)
listings_profile
listings_profile.to_file("listings_profile.html") #salva os resultados em um arquivo

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [20]:
listings_num.describe()

id     scrape_id       host_id  host_listings_count  \
count  3.196400e+04  3.196400e+04  3.196400e+04         31961.000000   
mean   3.514699e+17  2.023092e+13  1.663077e+08            16.112450   
std    3.999653e+17  8.242316e-01  1.684315e+08            89.082309   
min    1.787800e+04  2.023092e+13  1.671000e+03             1.000000   
25%    2.184739e+07  2.023092e+13  2.258631e+07             1.000000   
50%    5.261496e+07  2.023092e+13  8.693849e+07             2.000000   
75%    7.814279e+17  2.023092e+13  3.004090e+08             5.000000   
max    9.855551e+17  2.023092e+13  5.379850e+08          1311.000000   

       host_total_listings_count  neighbourhood_group_cleansed      latitude  \
count               31961.000000                           0.0  31964.000000   
mean                   27.273020                           NaN    -22.967574   
std                   134.207472                           NaN      0.035182   
min                     1.000000                           NaN    -23.073276   
25%                     1.000000                           NaN    -22.984820   
50%                     3.000000                           NaN    -22.972860   
75%                     7.000000                           NaN    -22.956165   
max                  1803.000000                           NaN    -22.749690   

          longitude  accommodates  bathrooms  ...  review_scores_checkin  \
count  31964.000000  31964.000000        0.0  ...           23668.000000   
mean     -43.251361      4.041265        NaN  ...               4.881593   
std        0.100595      2.370380        NaN  ...               0.321587   
min      -43.723009      1.000000        NaN  ...               1.000000   
25%      -43.310047      2.000000        NaN  ...               4.890000   
50%      -43.195670      4.000000        NaN  ...               5.000000   
75%      -43.185946      5.000000        NaN  ...               5.000000   
max      -43.104400     16.000000        NaN  ...               5.000000   

       review_scores_communication  review_scores_location  \
count                 23667.000000            23665.000000   
mean                      4.866827                4.861961   
std                       0.346049                0.322802   
min                       1.000000                1.000000   
25%                       4.870000                4.850000   
50%                       5.000000                4.980000   
75%                       5.000000                5.000000   
max                       5.000000                5.000000   

       review_scores_value  license  calculated_host_listings_count  \
count          23667.00000      0.0                    31964.000000   
mean               4.69660      NaN                        8.839319   
std                0.44839      NaN                       23.515196   
min                1.00000      NaN                        1.000000   
25%                4.61000      NaN                        1.000000   
50%                4.81000      NaN                        2.000000   
75%                5.00000      NaN                        4.000000   
max                5.00000      NaN                      163.000000   

       calculated_host_listings_count_entire_homes  \
count                                 31964.000000   
mean                                      8.010825   
std                                      23.328498   
min                                       0.000000   
25%                                       1.000000   
50%                                       1.000000   
75%                                       3.000000   
max                                     159.000000   

       calculated_host_listings_count_private_rooms  \
count                                  31964.000000   
mean                                       0.707139   
std                                        1.735520   
min                                        0.000000   
2

In [35]:
listings_not_num = listings.select_dtypes(exclude=['number'])
listings_not_num

listing_url last_scraped  \
0                  https://www.airbnb.com/rooms/231497   2023-09-22   
1                  https://www.airbnb.com/rooms/231516   2023-09-22   
2                  https://www.airbnb.com/rooms/236991   2023-09-23   
3                   https://www.airbnb.com/rooms/17878   2023-09-23   
4                   https://www.airbnb.com/rooms/25026   2023-09-22   
...                                                ...          ...   
31959  https://www.airbnb.com/rooms/985064291460771751   2023-09-22   
31960  https://www.airbnb.com/rooms/985340991466900379   2023-09-22   
31961  https://www.airbnb.com/rooms/985507696630141934   2023-09-22   
31962  https://www.airbnb.com/rooms/985510361579508644   2023-09-22   
31963  https://www.airbnb.com/rooms/985555107088259155   2023-09-23   

            source                                               name  \
0      city scrape  Rental unit in Rio de Janeiro · ★4.73 · 1 bedr...   
1      city scrape  Rental unit in Rio de Janeiro · ★4.71 · 1 bedr...   
2      city scrape  Rental unit in Rio de Janeiro · ★4.89 · 1 bedr...   
3      city scrape  Condo in Rio de Janeiro · ★4.70 · 2 bedrooms ·...   
4      city scrape  Rental unit in Rio de Janeiro · ★4.71 · 1 bedr...   
...            ...                                                ...   
31959  city scrape  Rental unit in Rio de Janeiro · ★New · 1 bedro...   
31960  city scrape  Rental unit in Rio de Janeiro · ★New · 2 bedro...   
31961  city scrape  Rental unit in Rio de Janeiro · ★New · 1 bedro...   
31962  city scrape  Rental unit in Rio de Janeiro · ★New · 2 bedro...   
31963  city scrape  Rental unit in Rio de Janeiro · ★New · 1 bedro...   

                                             description  \
0      This is a big studio at the end of Copacabana,...   
1      Special location of the building, on Copacaban...   
2      Aconchegante, amplo, básico, arejado, iluminad...   
3      Please note that elevated rates applies for Ne...   
4      **Fully renovated  in Dec 2022, new kitchen, n...   
...                                                  ...   
31959  Relaxe com toda a família nesta acomodação tra...   
31960  Hello!<br /><br />Season apartment, exclusive,...   
31961  O Apart-Hotel Villa Del Sol fica localizado na...   
31962  Apartamento amplo, com uma vaga de garagem. Lo...   
31963  <b>Other things to note</b><br />Season rental...   

                                   neighborhood_overview  \
0                                                    NaN   
1                                                    NaN   
2      Copacabana, apelidada a princesinha do mar, fa...   
3      This is the one of the bests spots in Rio. Bec...   
4      Copacabana is a lively neighborhood and the ap...   
...                                                  ...   
31959                                                NaN   
31960  Copacabana is a 24/7 neighborhood and very cha...   
31961                                                NaN   
31962  Rua residencial tranquila, a 4 quarteirões da ...   
31963                                                NaN   

                                             picture_url  \
0      https://a0.muscache.com/pictures/3582382/ee8ac...   
1      https://a0.muscache.com/pictures/3671683/d74b4...   
2      https://a0.muscache.com/pictures/5725a59b-147d...   
3      https://a0.muscache.com/pictures/65320518/3069...   
4      https://a0.muscache.com/pictures/a745aa21-b8dd...   
...                                                  ...   
31959  https://a0.muscache.com/pictures/hosting/Hosti...   
31960  https://a0.muscache.com/pictures/prohost-api/H...   
31961  https://a0.muscache.com/pictures/hosting/Hosti...   
31962  https://a0.muscache.com/pictures/hosting/Hosti...   
31963  https://a0.muscache.com/pictures/prohost-api/H...   

                                          host_url        host_name  \
0        https://www.airbnb.com/users/show/1207700      Maria Luiza   
1       

In [36]:
listings_not_num.columns

Index(['listing_url', 'last_scraped', 'source', 'name', 'description',
       'neighborhood_overview', 'picture_url', 'host_url', 'host_name',
       'host_since', 'host_location', 'host_about', 'host_response_time',
       'host_response_rate', 'host_acceptance_rate', 'host_is_superhost',
       'host_thumbnail_url', 'host_picture_url', 'host_neighbourhood',
       'host_verifications', 'host_has_profile_pic', 'host_identity_verified',
       'neighbourhood', 'neighbourhood_cleansed', 'property_type', 'room_type',
       'bathrooms_text', 'amenities', 'price', 'has_availability',
       'calendar_last_scraped', 'first_review', 'last_review',
       'instant_bookable'],
      dtype='object')

In [32]:
listings_not_num2 = listings_not_num.drop(columns=['description'])


In [39]:
listings_not_num['description'] = listings_not_num['description'].apply(lambda x: re.sub(r'[^a-zA-Z0-9]', ' ', x).lower() if isinstance(x, str) else x)


In [40]:
# Cria um relatório ProfileReport do dataframe
listings_profile = ProfileReport(listings_not_num, title="'Listings' Profiling Report", minimal=True)
listings_profile.to_file("listings_profile2.html") #salva os resultados em um arquivo

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [34]:
# Define uma função para converter as colunas para os tipos desejados
def transform_listings(df):
    df['description'] = df['description'].apply(lambda x: re.sub(r'[^a-zA-Z0-9]', ' ', x).lower() if isinstance(x, str) else x)

    
    # # Converte 'listing_id' para int
    # df['listing_id'] = df['listing_id'].astype(int)
    
    # # Converte 'minimum_nights' e 'maximum_nights' para int
    # df['minimum_nights'] = df['minimum_nights'].fillna(0).astype(int)
    # df['maximum_nights'] = df['maximum_nights'].fillna(0).astype(int)
    
    # # Remove vírgulas e o símbolo '$' e, em seguida, converte para float
    # df['price'] = df['price'].str.replace(',', '', regex=False).str.replace('$', '', regex=False).astype(float)
    # df['adjusted_price'] = df['adjusted_price'].str.replace(',', '', regex=False).str.replace('$', '', regex=False).astype(float)
    
    # # Converte 'date' para o tipo de data
    # df['date'] = pd.to_datetime(df['date'])
    
    # # Substituir 't' por 'Sim' e 'f' por 'Não' na coluna 'available'
    # df['available'] = df['available'].replace({'t': 'Sim', 'f': 'Não'})

  
    return df

# Aplica as transformações ao DataFrame
listings_b = listings.copy()
listings_t = transform_listings(listings_b)

Calendar

In [39]:
calendar.dtypes

listing_id          int64
date               object
available          object
price              object
adjusted_price     object
minimum_nights    float64
maximum_nights    float64
dtype: object

In [33]:
# Cria um relatório ProfileReport do dataframe
calendar_profile = ProfileReport(calendar, title="'Calendar' Profiling Report")
calendar_profile
#calendar_profile.to_file("calendar_profile.html") #salva os resultados em um arquivo

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [47]:
# Define uma função para converter as colunas para os tipos desejados
def transform_calendar(df):
    # Converte 'listing_id' para int
    df['listing_id'] = df['listing_id'].astype(int)
    
    # Converte 'minimum_nights' e 'maximum_nights' para int
    df['minimum_nights'] = df['minimum_nights'].fillna(0).astype(int)
    df['maximum_nights'] = df['maximum_nights'].fillna(0).astype(int)
    
    # Remove vírgulas e o símbolo '$' e, em seguida, converte para float
    df['price'] = df['price'].str.replace(',', '', regex=False).str.replace('$', '', regex=False).astype(float)
    df['adjusted_price'] = df['adjusted_price'].str.replace(',', '', regex=False).str.replace('$', '', regex=False).astype(float)
    
    # Converte 'date' para o tipo de data
    df['date'] = pd.to_datetime(df['date'])
    
    # Substituir 't' por 'Sim' e 'f' por 'Não' na coluna 'available'
    df['available'] = df['available'].replace({'t': 'Sim', 'f': 'Não'})

  
    return df

# Aplica as transformações ao DataFrame
calendar_b = calendar.copy()
calendar_t = transform_calendar(calendar_b)

In [48]:
calendar_t.head()

listing_id       date available  price  adjusted_price  minimum_nights  \
0       17878 2023-09-23       Não  265.0           265.0               5   
1       17878 2023-09-24       Sim  265.0           265.0               5   
2       17878 2023-09-25       Não  290.0           290.0               5   
3       17878 2023-09-26       Não  290.0           290.0               5   
4       17878 2023-09-27       Não  290.0           290.0               5   

   maximum_nights  
0              28  
1              28  
2              28  
3              28  
4              28

In [49]:
remove_duplicates(calendar_t)

N. de linhas antes de remover duplicadas: 11666976
N. de linhas depois de remover duplicadas: 11666976


In [52]:
check_miss(calendar_t)

listing_id        0.0
date              0.0
available         0.0
price             0.0
adjusted_price    0.0
minimum_nights    0.0
maximum_nights    0.0
dtype: float64

In [53]:
remove_constant(calendar_t)

N. de colunas antes de remover colunas constantes: 7
N. de colunas depois de remover colunas constantes: 7


In [56]:
verify_unbalanced(calendar_t)

[]

Reviews

In [57]:
reviews.dtypes

listing_id        int64
id                int64
date             object
reviewer_id       int64
reviewer_name    object
comments         object
dtype: object

In [13]:
# Cria um relatório ProfileReport do dataframe
reviews_profile = ProfileReport(reviews_t, title="'Reviews' Profiling Report")
reviews_profile
#calendar_profile.to_file("calendar_profile.html") #salva os resultados em um arquivo

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [58]:
reviews.head()

listing_id      id        date  reviewer_id reviewer_name  \
0      231497  726625  2011-11-17      1356783         Jenny   
1       17878   64852  2010-07-15       135370           Tia   
2       17878   76744  2010-08-11        10206          Mimi   
3       17878   91074  2010-09-06        80253           Jan   
4       17878  137528  2010-11-12       230449         Orene   

                                            comments  
0  Es un apartastudio muy bien ubicado. Tiene lo ...  
1  This apartment is in a perfect location -- two...  
2  we had a really great experience staying in Ma...  
3  Staying in Max appartment is like living in a ...  
4  In general very good and reasonable price.\r<b...

In [59]:
def transform_reviews(df):
    # Renomeando coluna 'id' para 'review_id'
    df = df.rename(columns={'id':'review_id'})
    
    # Converte 'listing_id', 'review_id', 'reviewer_id' para inteiros
    df['listing_id'] = df['listing_id'].astype(int)
    df['review_id'] = df['review_id'].astype(int)
    df['reviewer_id'] = df['reviewer_id'].astype(int)
    
    # Converte 'date' para o tipo de data
    df['date'] = pd.to_datetime(df['date'])
    
    # Limpa a coluna 'reviewer_name'
    df['reviewer_name'] = df['reviewer_name'].str.replace('[^a-zA-Z ]', '', regex=True)
    df['reviewer_name'] = df['reviewer_name'].str.title()
    
    # Limpa a coluna 'comments'
    df['comments'] = df['comments'].str.replace('[^a-zA-Z0-9,;.\s]', '', regex=True)
    df['comments'] = df['comments'].str.replace(r'<[^>]+>|[\\\/][^ ]+', '', regex=True)
    
    return df

reviews_b = reviews.copy()
reviews_t = transform_reviews(reviews_b)

In [60]:
reviews_t.head()

listing_id  review_id       date  reviewer_id reviewer_name  \
0      231497     726625 2011-11-17      1356783         Jenny   
1       17878      64852 2010-07-15       135370           Tia   
2       17878      76744 2010-08-11        10206          Mimi   
3       17878      91074 2010-09-06        80253           Jan   
4       17878     137528 2010-11-12       230449         Orene   

                                            comments  
0  Es un apartastudio muy bien ubicado. Tiene lo ...  
1  This apartment is in a perfect location  two b...  
2  we had a really great experience staying in Ma...  
3  Staying in Max appartment is like living in a ...  
4  In general very good and reasonable price.\rbr...

In [61]:
remove_duplicates(reviews_t)

N. de linhas antes de remover duplicadas: 637307
N. de linhas depois de remover duplicadas: 637307


In [62]:
check_miss(reviews_t)

listing_id       0.000000
review_id        0.000000
date             0.000000
reviewer_id      0.000000
reviewer_name    0.000000
comments         0.002981
dtype: float64

In [63]:
remove_constant(reviews_t)

N. de colunas antes de remover colunas constantes: 6
N. de colunas depois de remover colunas constantes: 6


In [64]:
verify_unbalanced(reviews_t)

[]

Silver

In [14]:
# Enviando as camadas silver para o banco de dados
listings_t.to_sql('airbnb_bronze', engine, if_exists='replace', index=False)
calendar_t.to_sql('airbnb_bronze', engine, if_exists='replace', index=False)
reviews_t.to_sql('airbnb_bronze', engine, if_exists='replace', index=False)

# ----------------------------------------------------------------------

In [22]:
# Realizando o merge dos dataframes dentro do banco de dados
query = """
SELECT *
FROM airbnb_listings
LEFT JOIN airbnb_calendar ON airbnb_listings.id = airbnb_calendar.listing_id;
"""
#LEFT JOIN airbnb_reviews ON airbnb_listings.id = airbnb_reviews.listing_id;

# Executando a consulta para obter o dataframe resultante do merge
df_merge = pd.read_sql_query(sql=sql_text(query), con=engine.connect())

In [ ]:
profile = ProfileReport(df_bronze, title="Pandas Profiling Report") #cria o relatório
profile
#profile.to_file("resultados.html") #salva os resultados em um arquiv

In [ ]:
# Prepara os tipos de cada coluna e depois armazena os resultados no banco na camada bronze

dict_dtype={'ID': sqlal.String(),
            'Customer_ID': sqlal.String(),
            'Month': sqlal.String(),
            'Name': sqlal.String(),
            'Age': sqlal.String(),
            'SSN': sqlal.String(),
            'Occupation': sqlal.String(),
            'Annual_Income': sqlal.String(),
            'Monthly_Inhand_Salary': sqlal.Float(),
            'Num_Bank_Accounts': sqlal.Integer(),
            'Num_Credit_Card': sqlal.Integer(),
            'Interest_Rate': sqlal.Integer(),
            'Num_of_Loan': sqlal.String(),
            'Type_of_Loan': sqlal.String(),
            'Delay_from_due_date': sqlal.Integer(),
            'Num_of_Delayed_Payment': sqlal.String(),
            'Changed_Credit_Limit': sqlal.String(),
            'Num_Credit_Inquiries': sqlal.Float(),
            'Credit_Mix': sqlal.String(),
            'Outstanding_Debt': sqlal.String(),
            'Credit_Utilization_Ratio': sqlal.Float(),   
            'Credit_History_Age': sqlal.String(),
            'Payment_of_Min_Amount': sqlal.String(),
            'Total_EMI_per_month': sqlal.Float(),
            'Amount_invested_monthly': sqlal.String(),
            'Payment_Behaviour': sqlal.String(),
            'Monthly_Balance': sqlal.String()}